In [1]:
# Notebook 3 : Analyse avec KMeans

import pandas as pd
import numpy as np 
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import plotly.graph_objects as go

In [2]:
# 1. Chargement des données
df = pd.read_csv('uber_dfclean.csv')

In [3]:

# 2. On se concentre sur le même échantillon que DBSCAN pour comparer
df_jeudi = df[df['weekday'] == 3][['Lat', 'Lon']]
df_sample = df_jeudi.sample(frac=0.1, random_state=42)
print("Taille de l'échantillon:", len(df_sample))

Taille de l'échantillon: 75514


In [4]:
# 3. Standardisation des données
scaler = StandardScaler()
X = scaler.fit_transform(df_sample)

In [5]:
# 4. Recherche du meilleur nombre de clusters avec la méthode du coude
inertias = []  # Pour stocker les WCSS (Within-Cluster Sum of Square)
silhouette_scores = []  # Pour stocker les scores silhouette
k_range = range(2, 100)

for k in k_range:
    print(f"Test avec {k} clusters...")
    kmeans = KMeans(n_clusters=k, random_state=42, n_init=10)
    kmeans.fit(X)
    inertias.append(kmeans.inertia_)
    score = silhouette_score(X, kmeans.labels_)
    silhouette_scores.append(score)

Test avec 2 clusters...
Test avec 3 clusters...
Test avec 4 clusters...
Test avec 5 clusters...
Test avec 6 clusters...
Test avec 7 clusters...
Test avec 8 clusters...
Test avec 9 clusters...
Test avec 10 clusters...
Test avec 11 clusters...
Test avec 12 clusters...
Test avec 13 clusters...
Test avec 14 clusters...
Test avec 15 clusters...
Test avec 16 clusters...
Test avec 17 clusters...
Test avec 18 clusters...
Test avec 19 clusters...
Test avec 20 clusters...
Test avec 21 clusters...
Test avec 22 clusters...
Test avec 23 clusters...
Test avec 24 clusters...
Test avec 25 clusters...
Test avec 26 clusters...
Test avec 27 clusters...
Test avec 28 clusters...
Test avec 29 clusters...
Test avec 30 clusters...
Test avec 31 clusters...
Test avec 32 clusters...
Test avec 33 clusters...
Test avec 34 clusters...
Test avec 35 clusters...
Test avec 36 clusters...
Test avec 37 clusters...
Test avec 38 clusters...
Test avec 39 clusters...
Test avec 40 clusters...
Test avec 41 clusters...
Test ave

In [8]:
# 4.1 Graphique de l'inertie (méthode du coude)
fig1 = go.Figure()
fig1.add_trace(go.Scatter(x=list(k_range), y=inertias,
                         mode='lines+markers',
                         name='Inertie'))
fig1.update_layout(title='Méthode du coude',
                  xaxis_title='Nombre de clusters',
                  yaxis_title='Inertie (WCSS)')
fig1.show()

In [9]:
# 4.2 Graphique du score silhouette
fig2 = go.Figure()
fig2.add_trace(go.Scatter(x=list(k_range), y=silhouette_scores,
                         mode='lines+markers',
                         name='Score Silhouette'))
fig2.update_layout(title='Score Silhouette par nombre de clusters',
                  xaxis_title='Nombre de clusters',
                  yaxis_title='Score Silhouette')
fig2.show()

Ces graphiques étendus jusqu'à 100 clusters nous donnent une meilleure vision et justifient nos choix précédents :

1. Score Silhouette :
- Pic initial à k=2 (0.65) mais non pertinent pour notre cas d'usage
- Stabilisation autour de 0.4 à partir de k=20
- La qualité des clusters reste relativement stable (0.38-0.4) même avec plus de clusters
- Pas de dégradation significative du score jusqu'à k=100

2. Méthode du coude (WCSS) :
- Forte diminution jusqu'à k=20
- "Coude" principal autour de k=20
- Diminution plus graduelle jusqu'à k=40
- Aplatissement progressif après k=40, mais continue à diminuer légèrement

Ces graphiques justifient mathématiquement notre choix de k=85 car :
1. Le score silhouette reste stable (~0.39)
2. L'inertie continue à diminuer même si faiblement
3. Nous sommes dans une zone où ajouter des clusters apporte encore des améliorations marginales

Conclusion :
Notre choix de k=85 est un bon compromis entre :
- Qualité statistique des clusters (score silhouette acceptable)
- Réduction significative de l'inertie
- Granularité nécessaire pour l'objectif business
- Le tout sans dégrader significativement les métriques de qualité

In [42]:
# 5. Application de KMeans avec le nombre optimal de clusters
# D'après les graphiques, on choisit 8 clusters (à adapter selon vos résultats)
n_clusters = 85
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
clusters = kmeans.fit_predict(X)

In [43]:
# 6. Visualisation des clusters
df_sample['cluster'] = clusters
fig3 = px.scatter_mapbox(df_sample,
                        lat='Lat',
                        lon='Lon',
                        color='cluster',
                        title=f'Clusters KMeans (k={n_clusters})',
                        size_max=15,
                        zoom=10,
                        mapbox_style="carto-positron")
fig3.show()


In [44]:
# 8. Centres des clusters
cluster_centers = df_sample.groupby('cluster').agg({
    'Lat': 'mean',
    'Lon': 'mean'
}).round(4)
print("\nCentres des clusters:")
print(cluster_centers)


Centres des clusters:
             Lat      Lon
cluster                  
0        40.7175 -74.0093
1        40.7664 -73.9189
2        40.7574 -73.9735
3        40.6462 -73.7838
4        40.6915 -74.1800
...          ...      ...
80       40.7612 -73.7741
81       40.6413 -74.1033
82       40.7840 -72.9929
83       40.8250 -73.9476
84       40.7457 -74.0330

[85 rows x 2 columns]


In [45]:
# Compter le nombre de points par cluster
cluster_sizes = df_sample['cluster'].value_counts()
print("\nTaille des clusters:")
print(cluster_sizes)


Taille des clusters:
cluster
79    4453
2     4294
40    3968
73    3805
27    3356
      ... 
62       4
55       3
52       2
31       2
23       1
Name: count, Length: 85, dtype: int64


In [ ]:
# Identifier les clusters ayant un nombre minimum de points
min_points = 200 # par exemple
significant_clusters = cluster_sizes[cluster_sizes >= min_points].index
filtered_df = df_sample[df_sample['cluster'].isin(significant_clusters)]

In [47]:
fig = px.scatter_mapbox(filtered_df,
                       lat="Lat",
                       lon="Lon",
                       color="cluster",
                       size_max=15,
                       zoom=10,
                       title="Clusters KMeans significatifs",
                       mapbox_style="carto-positron")
fig.show()

Cette visualisation avec k=85 clusters et un minimum de 260 points par cluster offre une segmentation particulièrement pertinente pour les chauffeurs Uber :

Distribution géographique optimisée :


Manhattan est divisé en zones distinctes et denses
Les quartiers périphériques (Brooklyn, Queens) sont bien représentés
Les zones sont de taille variable mais toujours significatives en termes de densité


Avantages opérationnels :


Chaque zone contient au moins 260 demandes, garantissant une activité substantielle
Les petites zones dans Manhattan reflètent une forte densité de demandes
Les zones plus larges en périphérie compensent par leur étendue une densité moindre


Intérêt pour les chauffeurs :


Les zones de petite taille indiquent des hotspots très actifs
La densité minimum de 260 points assure une rentabilité potentielle
La granularité fine permet une meilleure optimisation du positionnement

Cette approche combine donc efficacement :

Une segmentation fine là où l'activité est intense
Une garantie de volume minimal par zone
Une couverture complète des zones d'activité significative

→ C'est un excellent compromis entre précision géographique et viabilité opérationnelle pour les chauffeurs.

In [10]:
# 1. Sélection des données pour jeudi 17h
df_jeudi_17 = df[
    (df['weekday'] == 3) & 
    (df['hour'] == 17)
][['Lat', 'Lon']]

# 2. Échantillonnage 10%
df_sample = df_jeudi_17.sample(frac=0.1, random_state=42)
print("Taille de l'échantillon:", len(df_sample))

# 3. Standardisation
scaler = StandardScaler()
X = scaler.fit_transform(df_sample)

# 4. Calcul de l'inertie et du score silhouette
wcss = []
silhouette_scores = []
k_range = range(2, 100)

for k in k_range:
    kmeans = KMeans(n_clusters=k, random_state=42, n_init=10)
    kmeans.fit(X)
    wcss.append(kmeans.inertia_)
    score = silhouette_score(X, kmeans.predict(X))
    silhouette_scores.append(score)

# Visualisation méthode du coude
fig1 = px.line(x=list(k_range), y=wcss, 
               title='Méthode du coude - Jeudi 17h',
               labels={'x':'Nombre de clusters', 'y':'Inertie (WCSS)'})
fig1.show()

# Visualisation score silhouette
fig2 = px.line(x=list(k_range), y=silhouette_scores,
               title='Score Silhouette par nombre de clusters - Jeudi 17h',
               labels={'x':'Nombre de clusters', 'y':'Score Silhouette'})
fig2.show()

Taille de l'échantillon: 5670


In [12]:
# 5. Application de KMeans
n_clusters = 40  # notre nouveau choix pour 17h
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
df_sample['cluster'] = kmeans.fit_predict(X)

# 6. Calcul de la taille des clusters
cluster_sizes = df_sample['cluster'].value_counts()
print("\nTaille des clusters:")
print(cluster_sizes)

# 7. Filtrer les clusters significatifs
min_points = 200
significant_clusters = cluster_sizes[cluster_sizes >= min_points].index
df_filtered = df_sample[df_sample['cluster'].isin(significant_clusters)]

# 8. Visualisation
fig = px.scatter_mapbox(df_filtered,
                       lat='Lat',
                       lon='Lon',
                       color='cluster',
                       title='Clusters KMeans - Jeudi 17h (k=40, min_points=260)',
                       size_max=15,
                       zoom=10,
                       mapbox_style="carto-positron")
fig.show()

# 9. Afficher les centres des clusters
cluster_centers = df_filtered.groupby('cluster').agg({
    'Lat': 'mean',
    'Lon': 'mean'
}).round(4)
print("\nCentres des clusters:")
print(cluster_centers)


Taille des clusters:
cluster
27    616
1     606
36    598
23    525
15    486
0     371
4     339
14    259
29    250
32    225
20    219
6     141
8     127
13    124
37    119
34    118
12     76
2      73
10     68
33     64
25     61
7      39
30     39
11     22
22     21
24     13
3      13
35     11
9      11
26      8
38      7
31      6
19      4
16      4
17      2
21      1
28      1
5       1
39      1
18      1
Name: count, dtype: int64



Centres des clusters:
             Lat      Lon
cluster                  
0        40.7112 -74.0114
1        40.7534 -73.9759
4        40.7361 -73.9966
15       40.7535 -73.9904
23       40.7235 -74.0029
27       40.7613 -73.9731
36       40.7433 -73.9866


Pour 17h spécifiquement :

La carte montre une bonne répartition des clusters
Les zones sont bien définies malgré le seuil plus bas
La concentration sur Manhattan et les zones adjacentes est claire
Les différents quartiers sont bien représentés


Avantages de ce choix :

Meilleure cohérence entre les analyses de différentes heures
Permet de comparer les patterns entre créneaux horaires
Maintient une granularité suffisante pour l'aspect opérationnel

Cette visualisation avec k=40 et min_points=200 offre un bon compromis entre précision et pertinence opérationnelle pour l'heure de pointe.


# Conclusion : Choix final des modèles d'analyse

Après avoir exploré différentes approches de clustering (DBSCAN et KMeans) avec différents paramètres, nous pouvons tirer plusieurs conclusions :

1. Comparaison des algorithmes :
- DBSCAN :
  * Avantages : identifie naturellement les zones denses et les outliers
  * Limitations : tendance à créer un cluster dominant trop large (>80% des points)
  * Même avec eps=0.05, distribution déséquilibrée des clusters

- KMeans :
  * Meilleure distribution des zones
  * Plus adaptable aux besoins opérationnels
  * Permet un contrôle plus fin de la granularité

2. Paramètres optimaux retenus :
- Pour l'analyse globale (toute la journée) :
  * KMeans avec k=85 
  * Seuil minimum de 200 points par cluster
  * Justifié par la stabilisation du score silhouette (~0.39) et une inertie acceptable

- Pour les créneaux horaires spécifiques (ex: 17h) :
  * KMeans avec k=40
  * Même seuil de 200 points minimum
  * Adapté à la concentration des courses sur certaines zones

3. Justification des choix :
- Le seuil de 200 points assure :
  * Une activité suffisante par zone
  * La possibilité d'analyser différents créneaux horaires
  * Une flexibilité pour les périodes creuses

- Le nombre de clusters variable selon l'horaire permet :
  * Une meilleure adaptation aux patterns de demande
  * Une granularité pertinente pour chaque période
  * Un équilibre entre précision et opérationnalité

Cette approche combinée offre à Uber une vision optimisée pour le positionnement des chauffeurs, adaptable selon les moments de la journée tout en maintenant une cohérence d'analyse.